### Логлинейный анализ с контрастным (a.k.a. effect, deviant, sum-to-zero) кодированием 

Представленный скрипт позволяет получить оценки параметров __ненасыщенной__ логлинейной модели с контрастным кодированием и экспортировать их в excel. Для построения модели необходима база с выбранными переменными в формате .csv.

In [157]:
import pandas as pd
import statsmodels.formula.api as smf
import statsmodels.api as sm
from patsy.contrasts import Sum

In [158]:
dataset_name = input('Введите название csv-файла с базой данных: ')

if dataset_name[-4:] != '.csv':
    dataset_name += '.csv'

Введите название csv-файла с базой данных: lla_dz4_v1


В модуле statsmodels для построения модели используется не исходная база данных в виде объект\*признак, а таблица профилей частот. Следующие строки кода автоматически подготавливают такую таблицу из загруженных данных и, при необходимости, добавляют к значениям частот "дельту". Помните, что дельта необходима всегда при наличии в исходной таблице профилей нулевых частот. Отсутствие дельты в тех случаях, когда она нужна, оборачивается неадекватно высокими значениями стандартных ошибок параметров модели и - как следствие - неверной оценкой их значимости.

In [159]:
df = pd.read_csv(dataset_name, sep=';', na_values=' ', dtype='category').dropna()
df['count'] = 1

columns = [x for x in df.columns if x!='count']
pivot_table = df.groupby(columns).sum()
pivot_table['count'] = pivot_table['count'].fillna(0)
pivot_table.reset_index(inplace=True)
print('Исходная таблица профилей:')
pivot_table

Исходная таблица профилей:


party domicil edulvl  count
0      1       1      1    8.0
1      1       1      2   28.0
2      1       1      3   19.0
3      1       1      4  119.0
4      1       1      5  101.0
5      1       2      1   17.0
6      1       2      2   30.0
7      1       2      3   25.0
8      1       2      4   92.0
9      1       2      5   87.0
10     1       3      1   21.0
11     1       3      2   30.0
12     1       3      3   32.0
13     1       3      4   80.0
14     1       3      5   44.0
15     2       1      1    2.0
16     2       1      2    3.0
17     2       1      3    5.0
18     2       1      4   14.0
19     2       1      5   19.0
20     2       2      1    7.0
21     2       2      2    7.0
22     2       2      3    6.0
23     2       2      4   23.0
24     2       2      5   19.0
25     2       3      1    9.0
26     2       3      2    2.0
27     2       3      3    3.0
28     2       3      4   15.0
29     2       3      5    5.0
..   ...     ...    ...    ...
45     4       1      1    1.0
46     4       1      2    7.0
47     4       1      3    6.0
48     4       1      4   20.0
49     4       1      5   20.0
50     4       2      1    3.0
51     4       2      2    5.0
52     4       2      3    5.0
53     4       2      4   14.0
54     4       2      5   21.0
55     4       3      1    3.0
56     4       3      2    3.0
57     4       3      3    5.0
58     4       3      4   15.0
59     4       3      5    5.0
60     5       1      1    0.0
61     5       1      2    5.0
62     5       1      3    3.0
63     5       1      4   11.0
64     5       1      5   30.0
65     5       2      1    1.0
66     5       2      2    2.0
67     5       2      3    3.0
68     5       2      4   10.0
69     5       2      5   13.0
70     5       3      1    7.0
71     5       3      2    0.0
72     5       3      3    1.0
73     5       3      4    7.0
74     5       3      5    1.0

[75 rows x 4 columns]

In [160]:
print('В таблице найдено нулевых частот: ', len(pivot_table[pivot_table['count'] == 0.0]))
delta = float(input('Укажите значение дельты (например, 0.5): '))

В таблице найдено нулевых частот:  3
Укажите значение дельты (например, 0.5): 0.5


In [161]:
print('Таблица профилей с учетом дельты:')
pivot_table['count'] = pivot_table['count'] + delta
pivot_table

Таблица профилей с учетом дельты:


party domicil edulvl  count
0      1       1      1    8.5
1      1       1      2   28.5
2      1       1      3   19.5
3      1       1      4  119.5
4      1       1      5  101.5
5      1       2      1   17.5
6      1       2      2   30.5
7      1       2      3   25.5
8      1       2      4   92.5
9      1       2      5   87.5
10     1       3      1   21.5
11     1       3      2   30.5
12     1       3      3   32.5
13     1       3      4   80.5
14     1       3      5   44.5
15     2       1      1    2.5
16     2       1      2    3.5
17     2       1      3    5.5
18     2       1      4   14.5
19     2       1      5   19.5
20     2       2      1    7.5
21     2       2      2    7.5
22     2       2      3    6.5
23     2       2      4   23.5
24     2       2      5   19.5
25     2       3      1    9.5
26     2       3      2    2.5
27     2       3      3    3.5
28     2       3      4   15.5
29     2       3      5    5.5
..   ...     ...    ...    ...
45     4       1      1    1.5
46     4       1      2    7.5
47     4       1      3    6.5
48     4       1      4   20.5
49     4       1      5   20.5
50     4       2      1    3.5
51     4       2      2    5.5
52     4       2      3    5.5
53     4       2      4   14.5
54     4       2      5   21.5
55     4       3      1    3.5
56     4       3      2    3.5
57     4       3      3    5.5
58     4       3      4   15.5
59     4       3      5    5.5
60     5       1      1    0.5
61     5       1      2    5.5
62     5       1      3    3.5
63     5       1      4   11.5
64     5       1      5   30.5
65     5       2      1    1.5
66     5       2      2    2.5
67     5       2      3    3.5
68     5       2      4   10.5
69     5       2      5   13.5
70     5       3      1    7.5
71     5       3      2    0.5
72     5       3      3    1.5
73     5       3      4    7.5
74     5       3      5    1.5

[75 rows x 4 columns]

В statsmodels используется особый синтаксис для построения формул любых моделей. Так, чтобы переменные рассматривались как категориальные, нужно заключить их в скобки и добавить перед ними символ С: например, __C(variable)__. Для того чтобы категории этих переменных были закодированы по схеме sum-to-zero, заложенной в оригинальной модели логлинейного анализа Л. Гудмена, нужно дополнительно указать это в скобках следующим образом: __C(variable, Sum)__. Согласно используемому синтаксису, если между переменными поставить знак звездочки (\*), то в модель автоматически будут включены и все эффекты более низкого уровня для этих переменных: например, __C(variable_1, Sum)\*C(variable_2, Sum)__ означает, что в модели присутствуют сразу эффекты __C(variable_1, Sum)__, __C(variable_2, Sum)__ и __C(variable_1, Sum)\*C(variable_2, Sum)__. Поэтому в statsmodels нет необходимости прописывать все нужные эффекты вручную при построении иерархических моделей. Код ниже позволяет получить формулу в правильном формате для тех эффектов, которые выделил SPSS как generating class при процедуре отбора ненасыщенной модели.

In [162]:
formula = input('Укажите полученный generating class: ')

formula_new = 'count ~ C(' + formula.replace(', ',  ', Sum) + C(').replace('*', ', Sum)*C(') + ', Sum)'
print('Для указанной модели определена следующая формула: ', formula_new)

Укажите полученный generating class: party*domicil, domicil*edulvl
Для указанной модели определена следующая формула:  count ~ C(party, Sum)*C(domicil, Sum) + C(domicil, Sum)*C(edulvl, Sum)


Последние шаги - построение модели и сохранение оценок параметров микроэффектов и их p-value в excel при необходимости.

In [163]:
res = smf.glm(formula_new, pivot_table, family=sm.families.Poisson()).fit()
res.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                 Generalized Linear Model Regression Results                  
==============================================================================
Dep. Variable:                  count   No. Observations:                   75
Model:                            GLM   Df Residuals:                       48
Model Family:                 Poisson   Df Model:                           26
Link Function:                    log   Scale:                          1.0000
Method:                          IRLS   Log-Likelihood:                -172.90
Date:                Sun, 09 Dec 2018   Deviance:                       53.573
Time:                        22:55:42   Pearson chi2:                     55.9
No. Iterations:                     6   Covariance Type:             nonrobust
============================================================================================================
                                               coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------------------------------------
Intercept                                    2.0876      0.048     43.813      0.000       1.994       2.181
C(party, Sum)[S.1]                           1.5648      0.051     30.790      0.000       1.465       1.664
C(party, Sum)[S.2]                          -0.0766      0.078     -0.982      0.326      -0.229       0.076
C(party, Sum)[S.3]                          -0.8730      0.107     -8.129      0.000      -1.083      -0.663
C(party, Sum)[S.4]                          -0.1146      0.079     -1.449      0.147      -0.270       0.040
C(domicil, Sum)[S.1]                         0.0715      0.067      1.071      0.284      -0.059       0.202
C(domicil, Sum)[S.2]                         0.1011      0.065      1.543      0.123      -0.027       0.229
C(edulvl, Sum)[S.1]                         -0.7941      0.096     -8.255      0.000      -0.983      -0.606
C(edulvl, Sum)[S.2]                         -0.3406      0.077     -4.426      0.000      -0.491      -0.190
C(edulvl, Sum)[S.3]                         -0.3964      0.079     -5.038      0.000      -0.551      -0.242
C(edulvl, Sum)[S.4]                          0.8717      0.052     16.675      0.000       0.769       0.974
C(party, Sum)[S.1]:C(domicil, Sum)[S.1]     -0.1191      0.067     -1.766      0.077      -0.251       0.013
C(party, Sum)[S.2]:C(domicil, Sum)[S.1]     -0.2858      0.108     -2.639      0.008      -0.498      -0.074
C(party, Sum)[S.3]:C(domicil, Sum)[S.1]      0.1741      0.138      1.265      0.206      -0.096       0.444
C(party, Sum)[S.4]:C(domicil, Sum)[S.1]     -0.0313      0.105     -0.298      0.766      -0.237       0.175
C(party, Sum)[S.1]:C(domicil, Sum)[S.2]     -0.0383      0.071     -0.542      0.588      -0.177       0.100
C(party, Sum)[S.2]:C(domicil, Sum)[S.2]      0.2344      0.104      2.253      0.024       0.031       0.438
C(party, Sum)[S.3]:C(domicil, Sum)[S.2]     -0.1655      0.153     -1.081      0.280      -0.465       0.134
C(party, Sum)[S.4]:C(domicil, Sum)[S.2]      0.0277      0.109      0.254      0.799      -0.186       0.241
C(domicil, Sum)[S.1]:C(edulvl, Sum)[S.1]    -0.5829      0.154     -3.777      0.000      -0.885      -0.280
C(domicil, Sum)[S.2]:C(edulvl, Sum)[S.1]     0.0564      0.129      0.438      0.661      -0.196       0.309
C(domicil, Sum)[S.1]:C(edulvl, Sum)[S.2]     0.0623      0.109      0.571      0.568      -0.151       0.276
C(domicil, Sum)[S.2]:C(edulvl, Sum)[S.2]    -0.0388      0.107     -0.363      0.716      -0.248       0.171
C(domicil, Sum)[S.1]:C(edulvl, Sum)[S.3]    -0.1241      0.115     -1.075      0.283      -0.350       0.102
C(domicil, Sum)[S.2]:C(edulvl, Sum)[S.3]    -0.0497      0.109     -0.454      0.650      -0.264       0.165
C(domicil, Sum)[S.1]:C(edulvl, Sum)[S.4]     0.1724      0.074      2.317      0.020       0.027       0.318
C

In [164]:
level = float(input('Укажите уровень значимости для определения значимых микроэффектов (например, 0.05): '))
print('Всего найдено значимых эффектов (на заданном уровне значимости {}): '.format(level), 
      sum(res.pvalues.drop('Intercept') <= level))

Укажите уровень значимости для определения значимых микроэффектов (например, 0.05): 0.01
Всего найдено значимых эффектов (на заданном уровне значимости 0.01):  8


In [165]:
results = pd.DataFrame(columns=['Estimate', 'P-value'])
results['Estimate'] = round(res.params, 4)
results['P-value'] = round(res.pvalues, 4)
results.reset_index(inplace=True)
results.rename(columns={'index': 'Effect'}, inplace=True)
names = lambda x: x.replace(', Sum)[S.', '=').replace(']', ')').replace('C', '').replace(':', '*')
results['Effect'] = results['Effect'].apply(names)
results

Effect  Estimate  P-value
0                Intercept    2.0876   0.0000
1                (party=1)    1.5648   0.0000
2                (party=2)   -0.0766   0.3263
3                (party=3)   -0.8730   0.0000
4                (party=4)   -0.1146   0.1474
5              (domicil=1)    0.0715   0.2840
6              (domicil=2)    0.1011   0.1228
7               (edulvl=1)   -0.7941   0.0000
8               (edulvl=2)   -0.3406   0.0000
9               (edulvl=3)   -0.3964   0.0000
10              (edulvl=4)    0.8717   0.0000
11   (party=1)*(domicil=1)   -0.1191   0.0774
12   (party=2)*(domicil=1)   -0.2858   0.0083
13   (party=3)*(domicil=1)    0.1741   0.2058
14   (party=4)*(domicil=1)   -0.0313   0.7656
15   (party=1)*(domicil=2)   -0.0383   0.5878
16   (party=2)*(domicil=2)    0.2344   0.0242
17   (party=3)*(domicil=2)   -0.1655   0.2795
18   (party=4)*(domicil=2)    0.0277   0.7994
19  (domicil=1)*(edulvl=1)   -0.5829   0.0002
20  (domicil=2)*(edulvl=1)    0.0564   0.6612
21  (domicil=1)*(edulvl=2)    0.0623   0.5679
22  (domicil=2)*(edulvl=2)   -0.0388   0.7164
23  (domicil=1)*(edulvl=3)   -0.1241   0.2825
24  (domicil=2)*(edulvl=3)   -0.0497   0.6498
25  (domicil=1)*(edulvl=4)    0.1724   0.0205
26  (domicil=2)*(edulvl=4)   -0.0766   0.2903

In [147]:
results.to_excel('results.xlsx', index_label='ID')